In [ ]:

from google.colab import drive
drive.mount('/content/drive/')

Mounted at /content/drive/


In [ ]:
import os
os.chdir("/content/drive/MyDrive/CMPT733_Final_Project")
!ls

covid_19_data.csv			     state-geocodes-v2016.xls
preprocess_visualization_covid19_us_2.ipynb  us_counties_covid19_daily.csv
preprocess_visualization_covid19_us.ipynb    us_covid19_daily.csv
project.ipynb				     us_states_covid19_daily.csv


In [ ]:
!pip install geopandas==0.3.0
!pip install pyshp==1.2.10
!pip install shapely==1.6.3
!pip install plotly==4.14.3

In [ ]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import plotly.express as px
import plotly.graph_objects as go

In [ ]:

confirmed_df = pd.read_csv('https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_confirmed_global.csv')
deaths_df = pd.read_csv('https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_deaths_global.csv')
recoveries_df = pd.read_csv('https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_recovered_global.csv')
latest_data = pd.read_csv('https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_daily_reports/08-22-2020.csv')
us_medical_data = pd.read_csv('https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_daily_reports_us/08-22-2020.csv')

In [ ]:
confirmed_df = confirmed_df[confirmed_df['Country/Region']=='US']
deaths_df = deaths_df[deaths_df['Country/Region']=='US']
recoveries_df = recoveries_df[recoveries_df['Country/Region']=='US']

In [ ]:

base_stats = pd.DataFrame(columns=['Dates','Confirmed','Deaths','Recovered','Active'])
base_stats['Dates'] = confirmed_df.columns[4:]

base_stats['Confirmed'] = base_stats['Dates'].apply(lambda x: confirmed_df[x].sum())
base_stats['Deaths'] = base_stats['Dates'].apply(lambda x: deaths_df[x].sum())
base_stats['Recovered'] = base_stats['Dates'].apply(lambda x: recoveries_df[x].sum())
base_stats.reset_index(drop=False, inplace=True)
base_stats['Active'] = base_stats['index'].apply(lambda x: (base_stats['Confirmed'][x]-(base_stats['Deaths'][x]+base_stats['Recovered'][x])))
base_stats.head()

index    Dates  Confirmed  Deaths  Recovered  Active
0      0  1/22/20          1       0          0       1
1      1  1/23/20          1       0          0       1
2      2  1/24/20          2       0          0       2
3      3  1/25/20          2       0          0       2
4      4  1/26/20          5       0          0       5

In [ ]:
base_stats_fig = go.Figure()

for column in base_stats.columns.to_list()[2:6]:
    color_dict = {
      "Confirmed": "#118ab2",
      "Active": "#ef476f",
      "Recovered": "#06d6a0",
      "Deaths": "#073b4c"
        }
    base_stats_fig.add_trace(
        go.Scatter(
            x = base_stats['Dates'],
            y = base_stats[column],
            name = column,
            line = dict(color=color_dict[column]),
            hovertemplate ='<br><b>Date</b>: %{x}'+'<br><i>Count</i>:'+'%{y}',
        )
    )
    
for column in base_stats.columns.to_list()[2:6]:
    color_dict = {
      "Confirmed": "#149ECC",
      "Active": "#F47C98",
      "Recovered": "#24F9C1",
      "Deaths": "#0C6583"
        }
    base_stats_fig.add_trace(
        go.Scatter(
            x = base_stats['Dates'],
            y = base_stats['index'].apply(lambda x: (base_stats[column][x-7:x].sum())/7 if x>7 else (base_stats[column][0:x].sum())/7),
            name = column+" 7-day Moving Avg.",
            line = dict(dash="dash", color=color_dict[column]), showlegend=False,
            hovertemplate = '<br><b>Date</b>: %{x}'+'<br><i>7-day moving avg.</i>: %{y}'
        )
    )
    
base_stats_fig.update_layout(
    updatemenus=[
        dict(
        buttons=list(
            [dict(label = 'All Cases',
                  method = 'update',
                  args = [{'visible': [True, True, True, True, True, True, True, True]},
                          {'title': 'All Cases',
                           'showlegend':True}]),
             dict(label = 'Confirmed',
                  method = 'update',
                  args = [{'visible': [True, False, False, False, True, False, False, False]},
                          {'title': 'Confirmed',
                           'showlegend':True}]),
             dict(label = 'Active',
                  method = 'update',
                  args = [{'visible': [False, False, False, True, False, False, False, True]},
                          {'title': 'Active',
                           'showlegend':True}]),
             dict(label = 'Recovered',
                  method = 'update',
                  args = [{'visible': [False, False, True, False, False, False, True, False]},
                          {'title': 'Recovered',
                           'showlegend':True}]),
             dict(label = 'Deaths',
                  method = 'update',
                  args = [{'visible': [False, True, False, False, False, True, False, False]},
                          {'title': 'Deaths',
                           'showlegend':True}]),
            ]),
             type = "dropdown",
             direction="down",
#             pad={"r": 10, "t": 40},
             showactive=True,
             x=0,
             xanchor="left",
             y=1.25,
             yanchor="top"
        ),
        dict(
        buttons=list(
            [dict(label = 'Linear Scale',
                  method = 'relayout',
                  args = [{'yaxis': {'type': 'linear'}},
                          {'title': 'All Cases',
                           'showlegend':True}]),
             dict(label = 'Log Scale',
                  method = 'relayout',
                  args = [{'yaxis': {'type': 'log'}},
                          {'title': 'Confirmed',
                           'showlegend':True}]),
            ]),
             type = "dropdown",
             direction="down",
#             pad={"r": 10, "t": 10},
             showactive=True,
             x=0,
             xanchor="left",
             y=1.36,
             yanchor="top"
        )
    ])



base_stats_fig.update_xaxes(showticklabels=False)
base_stats_fig.update_layout(
    #height=600, width=600, 
    title_text="Basic Statistics for Covid19", title_x=0.5, title_font_size=20,
                            legend=dict(orientation='h',yanchor='top',y=1.15,xanchor='right',x=1), paper_bgcolor="mintcream",
                            xaxis_title="Date", yaxis_title="# of Cases")
base_stats_fig.show()


In [ ]:
corona_data=pd.read_csv('covid_19_data.csv')
choro_map=px.choropleth(corona_data, 
                    locations="Country/Region", 
                    locationmode = "country names",
                    color="Confirmed", 
                    hover_name="Country/Region", 
                    animation_frame="ObservationDate"
                   )

choro_map.update_layout(
    title_text = 'Global Spread of Coronavirus',
    title_x = 0.5,
    geo=dict(
        showframe = False,
        showcoastlines = False,
    ))
    
choro_map.show()

In [ ]:
state_covid_data=pd.read_csv('us_states_covid19_daily.csv')
state_covid_data = state_covid_data.sort_values(by = 'date')
covid_us_state_daily_cumulative_map=px.choropleth(state_covid_data, 
                    locations="state", 
                    locationmode = "USA-states",
                    color="positive",
                    scope = 'usa',  
                    animation_frame="date"
                   )

covid_us_state_daily_cumulative_map.update_layout(
    title_text = 'The Cumulative Changes of Covid-19 Spread in USA States',
    title_x = 0.5,
    )
    
covid_us_state_daily_cumulative_map.show()

In [ ]:

covid_us_daily_increase_map=px.choropleth(state_covid_data, 
                    locations="state", 
                    locationmode = "USA-states",
                    color="positiveIncrease",
                    scope = 'usa',  
                    animation_frame="date"
                   )

covid_us_daily_increase_map.update_layout(
    title_text = 'The Daily Increases of Covid-19 in USA States',
    title_x = 0.5,

    coloraxis_colorbar=dict(
        title = 'daily increase of positive cases',
        ticks="outside",
        tickmode = 'array',
        tickvals=[0,5000,10000,15000,20000,25000,30000 ],
        ticktext=["0", "5k", "10k", "15k", "20k", "25K", "30K"]
    ))
    
covid_us_daily_increase_map.show()